In [5]:
%pip install geocoder
%pip install leafmap
%pip install keplergl
%pip install geopandas
%pip install shapely
%pip install polyline shapely

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


Note: you may need to restart the kernel to use updated packages.


Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [6]:
import leafmap.kepler as leafmap
import geopandas as gpd
import pandas as pd
from shapely.geometry import LineString
import os
import requests
import polyline
import pandas as pd
from shapely.geometry import Point

In [7]:
departure = [33.1521436, -8.6055754]

m = leafmap.Map(center=departure, zoom=14, height=600)
m

In [8]:
import geocoder # pip install geocoder
g = geocoder.arcgis('London eye')
latlon = g.lat, g.lng
print(latlon)

(51.503303, -0.1195841)


In [9]:
df = pd.DataFrame({'longitude': [departure[1]] , 'latitude': [departure[0]]})
geometryDep = gpd.GeoSeries.from_xy(df.longitude, df.latitude , crs="EPSG:4326")
m = leafmap.Map(center=departure, zoom=12, height=1000, widescreen=False)
m.add_gdf(geometryDep, "Points", color="red")
m

Map(config={'version': 'v1', 'config': {'mapState': {'latitude': 33.1521436, 'longitude': -8.6055754, 'zoom': …

In [10]:
df= pd.read_csv('Big Data/DESTINATIONS.csv')
df.columns

Index(['DESTINATION_NUMBER', 'DESTINATION_NAME', 'DESTINATION_LOCATION',
       'LATITUDE', 'LONGITUDE'],
      dtype='object')

In [11]:
df['LATITUDE'] = pd.to_numeric(df['LATITUDE'])
df['LONGITUDE'] = pd.to_numeric(df['LONGITUDE'])

In [12]:
df = pd.DataFrame({'longitude': df.LONGITUDE , 'latitude': df.LATITUDE})
geometry = gpd.GeoSeries.from_xy(df.longitude, df.latitude , crs="EPSG:4326")
m = leafmap.Map(center=departure, zoom=12, height=1000, widescreen=False)
m.add_gdf(geometry, "Points")
m

Map(config={'version': 'v1', 'config': {'mapState': {'latitude': 33.1521436, 'longitude': -8.6055754, 'zoom': …

In [13]:
df = pd.read_csv('Big Data/DESTINATIONS.csv')
df= df.iloc[[2, 4, 7]]
df.loc[len(df)] = {'LONGITUDE': -8.6055754, 'LATITUDE': 33.1521436, 'DESTINATION_NAME':'DEPARTURE'}
df

DESTINATION_NUMBER             DESTINATION_NAME  \
2                 3.0                  Okay Energy   
4                 6.0      TotalEnergies ISMAILIYA   
7                 9.0  Guiri Afriquia Fuel Station   
3                 NaN                    DEPARTURE   

                        DESTINATION_LOCATION   LATITUDE  LONGITUDE  
2  https://maps.app.goo.gl/t754Yow6ZuL1ab1v6  33.133187  -8.482563  
4  https://maps.app.goo.gl/BgtVZb3mvS7W3q5cA  33.899022  -5.541286  
7  https://maps.app.goo.gl/ZicpnHz2ye5UPVyM9  33.047938  -8.688203  
3                                        NaN  33.152144  -8.605575

In [14]:
import pandas as pd
import requests
import polyline
import geopandas as gpd
from shapely.geometry import LineString

def main(df, departure, duration, distance):
    if 'LONGITUDE' not in df.columns or 'LATITUDE' not in df.columns:
        raise ValueError("DataFrame columns 'LONGITUDE' and 'LATITUDE' are required.")

    url = f"https://router.project-osrm.org/route/v1/driving/{departure[1]},{departure[0]};"
    df['LATITUDE'] = pd.to_numeric(df['LATITUDE'])
    df['LONGITUDE'] = pd.to_numeric(df['LONGITUDE'])
    for i in range(len(df)):
        url += str(df['LONGITUDE'].iloc[i]) + ',' + str(df['LATITUDE'].iloc[i]) + ';'
    url = url[:-1]  # Remove the last ';'
    url += "?overview=full"
    
    r = requests.get(url)
    data = r.json()
    print(url)
    # Save distance and duration
    distance[0] = data['routes'][0]['distance']
    duration[0] = data['routes'][0]['duration']
    try:
        encoded_polyline = data['routes'][0]['geometry']
        decoded_polyline = polyline.decode(encoded_polyline, 5)
        decoded_polyline = [t[::-1] for t in decoded_polyline]
        decoded_polyline = gpd.GeoSeries(LineString(decoded_polyline[::-1]), crs='4326')
        return decoded_polyline
    except (KeyError, IndexError):
        raise ValueError("No route found or invalid response from OSRM API.")

In [15]:
duration = [0]
distance = [0]
route = main(df,departure,duration,distance)

https://router.project-osrm.org/route/v1/driving/-8.6055754,33.1521436;-8.4825625,33.1331875;-5.5412857,33.8990221;-8.688203099999999,33.0479375;-8.6055754,33.1521436?overview=full


In [16]:
distance

[749643.5]

In [17]:
duration

[31905.4]

In [18]:
route

0    LINESTRING (-8.60532 33.15209, -8.60510 33.152...
dtype: geometry

In [19]:
df_copy = df.copy()
m = leafmap.Map(center=departure, zoom=12, height=600, widescreen=False)
m.add_gdf(route, "route")
geometry = gpd.GeoSeries.from_xy(df_copy['LONGITUDE'], df_copy['LATITUDE'] , crs="EPSG:4326")
m.add_gdf(geometry, "Points")
df_copy = pd.DataFrame({'longitude': [departure[1]] , 'latitude': [departure[0]]})
m

Map(config={'version': 'v1', 'config': {'mapState': {'latitude': 33.1521436, 'longitude': -8.6055754, 'zoom': …

In [20]:
df_copy = df.copy()
departure_coords = [-8.6055754,33.1521436 ]
m = leafmap.Map(center=departure, zoom=10, height=600, widescreen=False)
m.add_gdf(route, "route")
departure_geometry = gpd.GeoSeries(Point(departure_coords), crs="EPSG:4326")
geometry = gpd.GeoSeries.from_xy(df_copy['LONGITUDE'], df_copy['LATITUDE'], crs="EPSG:4326")
m.add_gdf(geometry, "Points")
m.add_gdf(departure_geometry, "Point")
df_copy = pd.DataFrame({'longitude': [departure[1]], 'latitude': [departure[0]]})
m

Map(config={'version': 'v1', 'config': {'mapState': {'latitude': 33.1521436, 'longitude': -8.6055754, 'zoom': …